In [1]:
import torch
import numpy as np
import json

In [2]:
def ensemble_triple(model_x, model_y, model_z, tokenizer_x, tokenizer_y, tokenizer_z, question, answer_text, alpha=.5):
    """
    Combines outputs from three transformers.
    NOTE: if tokenizer doesn't encode into a tuple / dict then make sure
    to unpack dictionary, input id's and input mask.
    Alpha must be smaller than .5.
    """

    # ======== Automated solution ========
    # Get token segment id's with encode plus
    max_len = 300

    input_dict_x = tokenizer_x.encode_plus(question, answer_text, max_length=max_len, truncation=True, padding='max_length', return_tensors='pt')
    input_dict_y = tokenizer_y.encode_plus(question, answer_text, max_length=max_len, truncation=True, padding='max_length', return_tensors='pt')
    input_dict_z = tokenizer_z.encode_plus(question, answer_text, max_length=max_len, truncation=True, padding='max_length', return_tensors='pt')

    # ======== Evaluate ========
    # Run our example question through the model.
    start_scores_x, end_scores_x = model_x(**input_dict_x)
    start_scores_y, end_scores_y = model_y(**input_dict_y)
    start_scores_z, end_scores_z = model_z(**input_dict_z)

    start = []
    start.append(torch.nn.functional.softmax(start_scores_x, dim=1).detach().numpy()[0])
    start.append(torch.nn.functional.softmax(start_scores_y, dim=1).detach().numpy()[0])
    start.append(torch.nn.functional.softmax(start_scores_z, dim=1).detach().numpy()[0])

    end = []
    end.append(torch.nn.functional.softmax(end_scores_x, dim=1).detach().numpy()[0])
    end.append(torch.nn.functional.softmax(end_scores_y, dim=1).detach().numpy()[0])
    end.append(torch.nn.functional.softmax(end_scores_z, dim=1).detach().numpy()[0])

    # model, start_ind, end_ind = ensemble_confidence_prob(start, end)
    # model, start_ind, end_ind = ensemble_confidence_score(start, end)


    # print("ANSWER: %d %d %d" %(model, start_ind, end_ind))

    # ======== Reconstruct Answer ========
    # Find the tokens with the highest `start` and `end` scores.
    # RANKS
    # mode = {'equal', 'ranks', 'f1'}
    model, answer_start, answer_end = combine_scores2(start, end, mode="equal")
    
    # There's a chance this might hit index out of bounds
    if model == 0:
      answer = tokenizer_x.decode(input_dict_x['input_ids'][0, answer_start:answer_end+1], skip_special_tokens=True)
    elif model == 1:
      answer = tokenizer_y.decode(input_dict_y['input_ids'][0, answer_start:answer_end+1], skip_special_tokens=True)
    else:
      answer = tokenizer_z.decode(input_dict_z['input_ids'][0, answer_start:answer_end+1], skip_special_tokens=True)
    # print('Answer: "' + answer + '"')
    return answer

In [3]:
def ensemble_confidence_score(start_scores, end_scores):
  prob, answer_start, answer_end, model = 0, 0, 0, 0
  for i in range(len(start_scores)):
    start = np.argmax(start_scores[i])
    end = np.argmax(end_scores[i])
    if (start_scores[i][start]*end_scores[i][end]) > prob:
      prob = start_scores[i][start]*end_scores[i][end]
      model = i 
      answer_start = start 
      answer_end = end 

  return model, answer_start, answer_end

def ensemble_confidence_prob(start_prob, end_prob):
  prob, answer_start, answer_end, model = 0.0, 0, 0, 0
  for i in range(len(start_prob)):
    # print("%f %f " %(max(start_prob[i]), max(end_prob[i])))
    for j in range(len(start_prob[i])):
      temp = start_prob[i][j] * end_prob[i]
      if max(temp) > prob:
        prob = max(temp)
        model = i
        answer_start = j
        answer_end = torch.argmax(torch.Tensor(temp))
    # print("%d %d %d %f" %(model, answer_start, answer_end, prob))

  return model, answer_start, answer_end

In [4]:
def ensemble_weighted_average_score(ranks, start_scores, end_scores):
  # use F1 ranks
  prob, answer_start, answer_end, model = 0.0, 0, 0, 0
  for i in range(len(start_scores)):
    start = np.argmax(start_scores[i])
    end = np.argmax(end_scores[i])
    if (ranks[i] * start_scores[i][start]*end_scores[i][end]) > prob:
      prob = ranks[i] * start_scores[i][start]*end_scores[i][end]
      model = i 
      answer_start = start 
      answer_end = end 
    # print("%d %d %d %f" %(model, answer_start, answer_end, prob))

  return model, answer_start, answer_end

def ensemble_weighted_average_prob(ranks, start_prob, end_prob):
  # use F1 ranks
  prob, answer_start, answer_end, model = 0.0, 0, 0, 0
  for i in range(len(start_prob)):
    for j in range(len(start_prob[i])):
      temp = ranks[i] * start_prob[i][j] * end_prob[i]
      if max(temp) > prob:
        prob = max(temp)
        model = i
        answer_start = j
        answer_end = torch.argmax(torch.Tensor(temp))
    # print("%d %d %d %f" %(model, answer_start, answer_end, prob))

  return model, answer_start, answer_end

def add_lists(tup):
  ans = tup[0]

  for i in range(1, len(tup)):
    np.add(ans, tup[i])

  return ans

def ensemble_weighted_average_new(ranks, start_prob, end_prob):
  prob, answer_start, answer_end, max_model, ans_val, max_start, max_end = [], 0, 0, 0, 0.0, 0, 0
  # number of models
  for i in range(len(start_prob)):
    # number of spans
    temp = []
    for j in range(len(start_prob[i])):
      t = ranks[i] * start_prob[i][j] * np.asarray(end_prob[i])
      temp.append(t)
      temp_val = max(t)
      if temp_val > ans_val:
        ans_val = temp_val 
        max_model = i
        max_start = j
        max_end = np.where(t == temp_val)
    
    prob.append(temp)

  # print(prob )
  answer_mat = np.asarray(prob[0])
  for i in range(1, len(prob)):
    answer_mat = np.add(answer_mat, np.asarray(prob[i]))

  # print(answer_mat)
  # print(answer_mat) 
  a = np.amax(answer_mat)
  answer_start = np.where(answer_mat == a)
  answer_end = int(answer_start[1][0])
  answer_start = int(answer_start[0][0])
    # print("%d %d %d %f" %(model, answer_start, answer_end, prob))

  return max_model, max_start, max_end, answer_start, answer_end

def combine_scores2(start_scores, end_scores, mode="equal"):
  if mode == "equal":
    l = len(start_scores)
    ranks = [1.0/l] * l
    model, max_start, max_end, start, end = ensemble_weighted_average_new(ranks, start_scores, end_scores)
    return model, start, end

  elif mode == "ranks":
    l = len(start_scores)
    ranks = list(range(1, l+1))
    l = l*(l+1)//2
    ranks = [x/float(l) for x in ranks]
    model, max_start, max_end, start, end = ensemble_weighted_average_new(ranks, start_scores, end_scores)
    return model, start, end

  elif mode == "f1":
    ranks = []
    model, max_start, max_end, start, end = ensemble_weighted_average_new(ranks, start_scores, end_scores)
    return model, start, end

In [5]:
from transformers import BertForQuestionAnswering, BertTokenizer

bert_mini_model = BertForQuestionAnswering.from_pretrained('mrm8488/bert-mini-5-finetuned-squadv2')
bert_mini_tokenizer = BertTokenizer.from_pretrained('mrm8488/bert-mini-5-finetuned-squadv2')
print("Bert Mini loaded...")

bert_small_model = BertForQuestionAnswering.from_pretrained('mrm8488/bert-small-finetuned-squadv2')
bert_small_tokenizer = BertTokenizer.from_pretrained('mrm8488/bert-small-finetuned-squadv2')
print("Bert Small loaded...")

bert_med_model = BertForQuestionAnswering.from_pretrained('mrm8488/bert-medium-finetuned-squadv2')
bert_med_tokenizer = BertTokenizer.from_pretrained('mrm8488/bert-medium-finetuned-squadv2')
print("Bert Medium loaded...")

Bert Mini loaded...
Bert Small loaded...
Bert Medium loaded...


In [6]:
def answer_question(question, text, alpha=.5):
  """
  Answering wrapper, change which function you use and which models you use it with
  """
  
  return ensemble_triple(bert_mini_model, bert_small_model, bert_med_model, 
                         bert_mini_tokenizer, bert_small_tokenizer, bert_med_tokenizer,question, text, alpha)

In [7]:
# Builtin preprocessor
from transformers.data.processors.squad import SquadV2Processor

processor = SquadV2Processor()
squad_data_dir='./SQUAD_V2'
eval_examples = processor.get_dev_examples(squad_data_dir,filename='dev-v2.0.json')

100%|██████████| 35/35 [00:05<00:00,  6.72it/s]


In [8]:
from tqdm import tqdm
for i,example in enumerate(tqdm(eval_examples)):
    if eval_examples[i].is_impossible:
        print(eval_examples[i].qas_id)
        print(eval_examples[i].question_text)
        print(eval_examples[i].context_text)
        print(eval_examples[i].answer_text)
        print(eval_examples[i].title)
        print(eval_examples[i].is_impossible)
        print(eval_examples[i].answers)
        print(eval_examples[i].start_position)
        print(eval_examples[i].end_position)

  2%|▏         | 288/11873 [00:00<00:04, 2434.21it/s]

5ad39d53604f3c001a3fe8d1
Who gave their name to Normandy in the 1000's and 1100's
The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.
None
Normans
True
[]
0
0
5ad39d53604f3c001a3fe8d2
What is France a region of?
The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10t

  6%|▌         | 699/11873 [00:00<00:05, 2218.09it/s]


Computational_complexity_theory
True
[]
0
0
5ad561c85b96ef001a10ad3e
What expression does not usually contain DTIME(n)?
For the complexity classes defined in this way, it is desirable to prove that relaxing the requirements on (say) computation time indeed defines a bigger set of problems. In particular, although DTIME(n) is contained in DTIME(n2), it would be interesting to know if the inclusion is strict. For time and space requirements, the answer to such questions is given by the time and space hierarchy theorems respectively. They are called hierarchy theorems because they induce a proper hierarchy on the classes defined by constraining the respective resources. Thus there are pairs of complexity classes such that one is properly included in the other. Having deduced such proper set inclusions, we can proceed to make quantitative statements about how much more additional time or space is needed in order to increase the number of problems that can be solved.
None
Computational_com

 10%|▉         | 1147/11873 [00:00<00:04, 2216.13it/s]

...

0
0
5ad4d9be5b96ef001a10a3b0
What style was he Paris Philharmony edifice built in?
Exceptional examples of the bourgeois architecture of the later periods were not restored by the communist authorities after the war (like mentioned Kronenberg Palace and Insurance Company Rosja building) or they were rebuilt in socialist realism style (like Warsaw Philharmony edifice originally inspired by Palais Garnier in Paris). Despite that the Warsaw University of Technology building (1899–1902) is the most interesting of the late 19th-century architecture. Some 19th-century buildings in the Praga district (the Vistula’s right bank) have been restored although many have been poorly maintained. Warsaw’s municipal government authorities have decided to rebuild the Saxon Palace and the Brühl Palace, the most distinctive buildings in prewar Warsaw.
None
Warsaw
True
[]
0
0
5ad4d9be5b96ef001a10a3b1
What were the Saxon Palace and Bruhl Palace in prewar Paris?
Exceptional examples of the bourgeois architec

 96%|█████████▌| 11380/11873 [00:05<00:00, 1874.49it/s]

5ad3a79a604f3c001a3fead7
What was abnormal British defense?
At the start of the war, no French regular army troops were stationed in North America, and few British troops. New France was defended by about 3,000 troupes de la marine, companies of colonial regulars (some of whom had significant woodland combat experience). The colonial government recruited militia support when needed. Most British colonies mustered local militia companies, generally ill trained and available only for short periods, to deal with native threats, but did not have any standing forces.
None
French_and_Indian_War
True
[]
0
0
5ad3a7ef604f3c001a3feadd
What was intent of Celeron's expedition?
Céloron's expedition force consisted of about 200 Troupes de la marine and 30 Indians. The expedition covered about 3,000 miles (4,800 km) between June and November 1749. It went up the St. Lawrence, continued along the northern shore of Lake Ontario, crossed the portage at Niagara, and followed the southern shore of Lake Er

100%|██████████| 11873/11873 [00:05<00:00, 2025.59it/s]


0
5ad3bb12604f3c001a3feebd
What naval battles did France lose in 1795?
In the aftermath of generally poor French results in most theaters of the Seven Years' War in 1758, France's new foreign minister, the duc de Choiseul, decided to focus on an invasion of Britain, to draw British resources away from North America and the European mainland. The invasion failed both militarily and politically, as Pitt again planned significant campaigns against New France, and sent funds to Britain's ally on the mainland, Prussia, and the French Navy failed in the 1759 naval battles at Lagos and Quiberon Bay. In one piece of good fortune, some French supply ships managed to depart France, eluding the British blockade of the French coast.
None
French_and_Indian_War
True
[]
0
0
5ad3bb68604f3c001a3feec3
Who was defeated by Montcalm at Quebec?
British victories continued in all theaters in the Annus Mirabilis of 1759, when they finally captured Ticonderoga, James Wolfe defeated Montcalm at Quebec (in a ba

In [9]:
from transformers import squad_convert_examples_to_features
# from transformers.data.processors.squad import squad_convert_examples_to_features

In [10]:
# import multiprocessing
# features, dataset = squad_convert_examples_to_features(
#             examples=eval_examples,
#             tokenizer=bert_mini_tokenizer,
#             max_seq_length=384,
#             doc_stride=128,
#             max_query_length=100,
#             is_training=False,
#             return_dataset="pt",
#             threads=multiprocessing.cpu_count(),
#         )

In [11]:
"""
self.qas_id = qas_id
self.question_text = question_text
self.context_text = context_text
self.answer_text = answer_text
self.title = title
self.is_impossible = is_impossible
self.answers = answers
"""
print(eval_examples[0].qas_id)
print(eval_examples[0].question_text)
print(eval_examples[0].context_text)
print(eval_examples[0].answer_text)
print(eval_examples[0].title)
print(eval_examples[0].is_impossible)
print(eval_examples[0].answers)

56ddde6b9a695914005b9628
In what country is Normandy located?
The Normans (Norman: Nourmands; French: Normands; Latin: Normanni) were the people who in the 10th and 11th centuries gave their name to Normandy, a region in France. They were descended from Norse ("Norman" comes from "Norseman") raiders and pirates from Denmark, Iceland and Norway who, under their leader Rollo, agreed to swear fealty to King Charles III of West Francia. Through generations of assimilation and mixing with the native Frankish and Roman-Gaulish populations, their descendants would gradually merge with the Carolingian-based cultures of West Francia. The distinct cultural and ethnic identity of the Normans emerged initially in the first half of the 10th century, and it continued to evolve over the succeeding centuries.
None
Normans
False
[{'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}, {'text': 'France', 'answer_start': 159}]


In [12]:
from tqdm import tqdm
def run_predictions(eval_set, out_filename, n_examples=None, padding=False):
  """
  Automatic prediction script with options for checkpointing, error coverage,
  padding of incomplete experiments and filedumping.
  """
  predictions = dict()
  error_count = 0

  if not n_examples:
    for i, example in enumerate(tqdm(eval_set)):
      try:
        predictions[example.qas_id] = answer_question(example.question_text, example.context_text)
      except:
        predictions[example.qas_id] = ""
        error_count += 1
  else:
    for i in tqdm(range(n_examples)):
      example = eval_set[i]
      predictions[example.qas_id] = answer_question(example.question_text, example.context_text)
        
    if padding:
      for i in range(n_examples, len(eval_set), 1):
        example = eval_set[i]
        predictions[example.qas_id] = ""

  with open('./SQUAD_V2/'+out_filename, 'w') as fp:
      json.dump(predictions, fp)

In [13]:
run_predictions(eval_examples, "mini_small_med_eq.json")
print("Done")

100%|██████████| 11873/11873 [1:14:18<00:00,  2.66it/s]    

Done


In [14]:
import argparse
import collections
import json
import numpy as np
import os
import re
import string
import sys

In [15]:
class Config(object):
    def __init__(self,):
        self.data_file='./SQUAD_V2/dev-v2.0.json'
        self.pred_file='./SQUAD_V2/mini_small_med_eq.json'
        self.out_file='./SQUAD_V2/eval.json'
        self.na_prob_file=None
        self.na_prob_thresh=1.0
        self.out_image_dir='./SQUAD_V2'
OPTS=Config()

In [16]:
def make_qid_to_has_ans(dataset):
  qid_to_has_ans = {}
  for article in dataset:
    for p in article['paragraphs']:
      for qa in p['qas']:
        qid_to_has_ans[qa['id']] = bool(qa['answers'])
  return qid_to_has_ans

def normalize_answer(s):
  """Lower text and remove punctuation, articles and extra whitespace."""
  def remove_articles(text):
    regex = re.compile(r'\b(a|an|the)\b', re.UNICODE)
    return re.sub(regex, ' ', text)
  def white_space_fix(text):
    return ' '.join(text.split())
  def remove_punc(text):
    exclude = set(string.punctuation)
    return ''.join(ch for ch in text if ch not in exclude)
  def lower(text):
    return text.lower()
  return white_space_fix(remove_articles(remove_punc(lower(s))))

def get_tokens(s):
  if not s: return []
  return normalize_answer(s).split()

def compute_exact(a_gold, a_pred):
  return int(normalize_answer(a_gold) == normalize_answer(a_pred))

def compute_f1(a_gold, a_pred):
  gold_toks = get_tokens(a_gold)
  pred_toks = get_tokens(a_pred)
  common = collections.Counter(gold_toks) & collections.Counter(pred_toks)
  num_same = sum(common.values())
  if len(gold_toks) == 0 or len(pred_toks) == 0:
    # If either is no-answer, then F1 is 1 if they agree, 0 otherwise
    return int(gold_toks == pred_toks)
  if num_same == 0:
    return 0
  precision = 1.0 * num_same / len(pred_toks)
  recall = 1.0 * num_same / len(gold_toks)
  f1 = (2 * precision * recall) / (precision + recall)
  return f1

def get_raw_scores(dataset, preds):
  exact_scores = {}
  f1_scores = {}
  for article in dataset:
    for p in article['paragraphs']:
      for qa in p['qas']:
        qid = qa['id']
        gold_answers = [a['text'] for a in qa['answers']
                        if normalize_answer(a['text'])]
        if not gold_answers:
          # For unanswerable questions, only correct answer is empty string
          gold_answers = ['']
        if qid not in preds:
          print('Missing prediction for %s' % qid)
          continue
        a_pred = preds[qid]
        # Take max over all gold answers
        exact_scores[qid] = max(compute_exact(a, a_pred) for a in gold_answers)
        f1_scores[qid] = max(compute_f1(a, a_pred) for a in gold_answers)
  return exact_scores, f1_scores

def apply_no_ans_threshold(scores, na_probs, qid_to_has_ans, na_prob_thresh):
  new_scores = {}
  for qid, s in scores.items():
    pred_na = na_probs[qid] > na_prob_thresh
    if pred_na:
      new_scores[qid] = float(not qid_to_has_ans[qid])
    else:
      new_scores[qid] = s
  return new_scores

def make_eval_dict(exact_scores, f1_scores, qid_list=None):
  if not qid_list:
    total = len(exact_scores)
    return collections.OrderedDict([
        ('exact', 100.0 * sum(exact_scores.values()) / total),
        ('f1', 100.0 * sum(f1_scores.values()) / total),
        ('total', total),
    ])
  else:
    total = len(qid_list)
    return collections.OrderedDict([
        ('exact', 100.0 * sum(exact_scores[k] for k in qid_list) / total),
        ('f1', 100.0 * sum(f1_scores[k] for k in qid_list) / total),
        ('total', total),
    ])

def merge_eval(main_eval, new_eval, prefix):
  for k in new_eval:
    main_eval['%s_%s' % (prefix, k)] = new_eval[k]

def plot_pr_curve(precisions, recalls, out_image, title):
  plt.step(recalls, precisions, color='b', alpha=0.2, where='post')
  plt.fill_between(recalls, precisions, step='post', alpha=0.2, color='b')
  plt.xlabel('Recall')
  plt.ylabel('Precision')
  plt.xlim([0.0, 1.05])
  plt.ylim([0.0, 1.05])
  plt.title(title)
  plt.savefig(out_image)
  plt.clf()

def make_precision_recall_eval(scores, na_probs, num_true_pos, qid_to_has_ans,
                               out_image=None, title=None):
  qid_list = sorted(na_probs, key=lambda k: na_probs[k])
  true_pos = 0.0
  cur_p = 1.0
  cur_r = 0.0
  precisions = [1.0]
  recalls = [0.0]
  avg_prec = 0.0
  for i, qid in enumerate(qid_list):
    if qid_to_has_ans[qid]:
      true_pos += scores[qid]
    cur_p = true_pos / float(i+1)
    cur_r = true_pos / float(num_true_pos)
    if i == len(qid_list) - 1 or na_probs[qid] != na_probs[qid_list[i+1]]:
      # i.e., if we can put a threshold after this point
      avg_prec += cur_p * (cur_r - recalls[-1])
      precisions.append(cur_p)
      recalls.append(cur_r)
  if out_image:
    plot_pr_curve(precisions, recalls, out_image, title)
  return {'ap': 100.0 * avg_prec}

def run_precision_recall_analysis(main_eval, exact_raw, f1_raw, na_probs, 
                                  qid_to_has_ans, out_image_dir):
  if out_image_dir and not os.path.exists(out_image_dir):
    os.makedirs(out_image_dir)
  num_true_pos = sum(1 for v in qid_to_has_ans.values() if v)
  if num_true_pos == 0:
    return
  pr_exact = make_precision_recall_eval(
      exact_raw, na_probs, num_true_pos, qid_to_has_ans,
      out_image=os.path.join(out_image_dir, 'pr_exact.png'),
      title='Precision-Recall curve for Exact Match score')
  pr_f1 = make_precision_recall_eval(
      f1_raw, na_probs, num_true_pos, qid_to_has_ans,
      out_image=os.path.join(out_image_dir, 'pr_f1.png'),
      title='Precision-Recall curve for F1 score')
  oracle_scores = {k: float(v) for k, v in qid_to_has_ans.items()}
  pr_oracle = make_precision_recall_eval(
      oracle_scores, na_probs, num_true_pos, qid_to_has_ans,
      out_image=os.path.join(out_image_dir, 'pr_oracle.png'),
      title='Oracle Precision-Recall curve (binary task of HasAns vs. NoAns)')
  merge_eval(main_eval, pr_exact, 'pr_exact')
  merge_eval(main_eval, pr_f1, 'pr_f1')
  merge_eval(main_eval, pr_oracle, 'pr_oracle')

def histogram_na_prob(na_probs, qid_list, image_dir, name):
  if not qid_list:
    return
  x = [na_probs[k] for k in qid_list]
  weights = np.ones_like(x) / float(len(x))
  plt.hist(x, weights=weights, bins=20, range=(0.0, 1.0))
  plt.xlabel('Model probability of no-answer')
  plt.ylabel('Proportion of dataset')
  plt.title('Histogram of no-answer probability: %s' % name)
  plt.savefig(os.path.join(image_dir, 'na_prob_hist_%s.png' % name))
  plt.clf()

def find_best_thresh(preds, scores, na_probs, qid_to_has_ans):
  num_no_ans = sum(1 for k in qid_to_has_ans if not qid_to_has_ans[k])
  cur_score = num_no_ans
  best_score = cur_score
  best_thresh = 0.0
  qid_list = sorted(na_probs, key=lambda k: na_probs[k])
  for i, qid in enumerate(qid_list):
    if qid not in scores: continue
    if qid_to_has_ans[qid]:
      diff = scores[qid]
    else:
      if preds[qid]:
        diff = -1
      else:
        diff = 0
    cur_score += diff
    if cur_score > best_score:
      best_score = cur_score
      best_thresh = na_probs[qid]
  return 100.0 * best_score / len(scores), best_thresh

def find_all_best_thresh(main_eval, preds, exact_raw, f1_raw, na_probs, qid_to_has_ans):
  best_exact, exact_thresh = find_best_thresh(preds, exact_raw, na_probs, qid_to_has_ans)
  best_f1, f1_thresh = find_best_thresh(preds, f1_raw, na_probs, qid_to_has_ans)
  main_eval['best_exact'] = best_exact
  main_eval['best_exact_thresh'] = exact_thresh
  main_eval['best_f1'] = best_f1
  main_eval['best_f1_thresh'] = f1_thresh

In [17]:
  with open(OPTS.data_file) as f:
    dataset_json = json.load(f)
    dataset = dataset_json['data']
  with open(OPTS.pred_file) as f:
    preds = json.load(f)
  if OPTS.na_prob_file:
    with open(OPTS.na_prob_file) as f:
      na_probs = json.load(f)
  else:
    na_probs = {k: 0.0 for k in preds}
  qid_to_has_ans = make_qid_to_has_ans(dataset)  # maps qid to True/False
  has_ans_qids = [k for k, v in qid_to_has_ans.items() if v]
  no_ans_qids = [k for k, v in qid_to_has_ans.items() if not v]
  exact_raw, f1_raw = get_raw_scores(dataset, preds)
  exact_thresh = apply_no_ans_threshold(exact_raw, na_probs, qid_to_has_ans,
                                        OPTS.na_prob_thresh)
  f1_thresh = apply_no_ans_threshold(f1_raw, na_probs, qid_to_has_ans,
                                     OPTS.na_prob_thresh)
  out_eval = make_eval_dict(exact_thresh, f1_thresh)
  if has_ans_qids:
    has_ans_eval = make_eval_dict(exact_thresh, f1_thresh, qid_list=has_ans_qids)
    merge_eval(out_eval, has_ans_eval, 'HasAns')
  if no_ans_qids:
    no_ans_eval = make_eval_dict(exact_thresh, f1_thresh, qid_list=no_ans_qids)
    merge_eval(out_eval, no_ans_eval, 'NoAns')
  if OPTS.na_prob_file:
    find_all_best_thresh(out_eval, preds, exact_raw, f1_raw, na_probs, qid_to_has_ans)
  if OPTS.na_prob_file and OPTS.out_image_dir:
    run_precision_recall_analysis(out_eval, exact_raw, f1_raw, na_probs, 
                                  qid_to_has_ans, OPTS.out_image_dir)
    histogram_na_prob(na_probs, has_ans_qids, OPTS.out_image_dir, 'hasAns')
    histogram_na_prob(na_probs, no_ans_qids, OPTS.out_image_dir, 'noAns')
  if OPTS.out_file:
    with open(OPTS.out_file, 'w') as f:
      json.dump(out_eval, f)
  else:
    print(json.dumps(out_eval, indent=2))